## Qwen on halubench 1200

In [ ]:
import os
import json
import csv
import pandas as pd
import torch
from typing import List, Optional, Any, Iterable
from transformers import AutoModelForCausalLM, AutoTokenizer

# ========= CONFIG =========
INPUT_CSV = 'output_files/halubench/halubench_combined_results_with_1200_full_texts.csv'  # must contain: question, hybrid_full_text, contriever_full_text
OUTPUT_HYBRID_CSV = "output_files/halubench/halubench_answers_hybrid_qwen3_4b_1200rows.csv"
OUTPUT_CONTRIEVER_CSV = "output_files/halubench/halubench_answers_contriever_qwen3_4b_1200rows.csv"

# Only process first N rows when testing. Set to None to process all.
TEST_LIMIT: Optional[int] = None  # set None for full run

QUESTION_COL = "question"
HYBRID_CTX_COL = "hybrid_full_text"
CONTRIEVER_CTX_COL = "contriever_full_text"

# MODEL: switched to Qwen 3 4B Instruct
MODEL_ID = "Qwen/Qwen3-4B-Instruct-2507"
DEVICE = "cuda" if torch.cuda.is_available() else "cpu"

# Inference/runtime knobs
MAX_NEW_TOKENS = 256
SEED = 42

# Debug: print the exact prompt fed to the model
DEBUG_PROMPTS = True
PROMPT_LOG = None  # e.g., "prompt_log.txt" to save to file; keep None to print to stdout

# Optional: clip long context to avoid OOM
MAX_CTX_CHARS_PER_ITEM = 2000  # clip each item; adjust as needed

# If your context columns are delimiter-separated strings (not JSON), set a delimiter here.
# If None, we will try JSON first; if that fails, treat the whole cell as one item.
CONTEXT_SPLIT_DELIM: Optional[str] = None  # e.g., " ||| " or "\n\n"

ENCODING = "utf-8"
NEWLINE = ""  # important for csv on Windows

torch.manual_seed(SEED)
# ==========================

# ---------- Load model + tokenizer ----------
tokenizer = AutoTokenizer.from_pretrained(MODEL_ID, use_fast=True)
# Ensure pad token exists (common for Qwen)
if tokenizer.pad_token_id is None and tokenizer.eos_token_id is not None:
    tokenizer.pad_token = tokenizer.eos_token

model = AutoModelForCausalLM.from_pretrained(
    MODEL_ID,
    torch_dtype=torch.float16 if torch.cuda.is_available() else torch.float16,
    device_map="auto"  # may offload to CPU if VRAM insufficient
)
if DEVICE != "cuda":
    model.to(DEVICE)

# ---------- Helpers to normalize context into a list of items ----------
def normalize_context_to_list(val: Any) -> List[str]:
    """
    Converts the cell value into a list of strings (context items).
    Accepts:
      - JSON array of strings
      - JSON array of dicts with "full_text" (will extract the strings)
      - Delimiter-separated string if CONTEXT_SPLIT_DELIM is set
      - Plain string (returns [string])
      - list[str]
      - list[dict] with "full_text"
    """
    if val is None or (isinstance(val, float) and pd.isna(val)):
        return []

    if isinstance(val, list):
        items = []
        for item in val:
            if isinstance(item, dict):
                if "full_text" in item and isinstance(item["full_text"], str):
                    items.append(item["full_text"])
            elif isinstance(item, str):
                items.append(item)
        return [s for s in items if s and str(s).strip()]

    if isinstance(val, dict):
        for k in ["docs", "results", "items", "data"]:
            if k in val and isinstance(val[k], list):
                return normalize_context_to_list(val[k])
        if "full_text" in val and isinstance(val["full_text"], str):
            return [val["full_text"]]
        return []

    if isinstance(val, str):
        s = val.strip()
        if s.startswith("[") or s.startswith("{"):
            try:
                parsed = json.loads(s)
                return normalize_context_to_list(parsed)
            except Exception:
                pass
        if CONTEXT_SPLIT_DELIM is not None and CONTEXT_SPLIT_DELIM in s:
            parts = [p.strip() for p in s.split(CONTEXT_SPLIT_DELIM)]
            return [p for p in parts if p]
        return [s]

    return [str(val)]

# ---------- Structured Prompt builder ----------
def build_structured_prompt(question: str, context_items: List[str]) -> str:
    labeled_lines = []
    for i, txt in enumerate(context_items, start=1):
        tx = str(txt)
        if MAX_CTX_CHARS_PER_ITEM is not None:
            tx = tx[:MAX_CTX_CHARS_PER_ITEM]
        clean = " ".join(tx.split())
        labeled_lines.append(f"[context {i}] - {clean}")
    contexts_block = "\n".join(labeled_lines) if labeled_lines else ""

    prompt = (
        "You are a helpful assistant. Follow the user's instructions carefully and answer the question in one or max two sentences. "
        "Do not repeat any part of the prompt in your final answer and answer strictly based on provided contexts.\n\n"
        "Prompt:\n"
        f"Question:- {question}\n"
        "Contexts:-\n"
        f"{contexts_block}\n\n"
        "Your task is to answer the given question by thinking progressively following the steps:\n"
        "Step 0: Process the answer within your memory and only provide the necessary answer.\n"
        "Step 1: Carefully read and understand the question and given contexts which can support you to answer better.\n"
        "Step 2: Analyze whether the given contexts provides sufficient information to answer the question.\n"
        "- If the given contexts do not provide sufficient information, respond with: “The context does not provide sufficient information to answer the question.”\n"
        "- If the given contexts provide sufficient information, proceed to Step 3.\n"
        "Step 3: Generate an accurate and grounded response strictly based on the provided contexts. Avoid guessing or providing incorrect/hallucinated responses.\n"
        "Step 4: Only when you are sure of Step 3, Clearly state the final answer in one or two sentences.\n\n"
        "Answer:"
    )
    return prompt

def generate_answer(question: str, context_text: Any) -> str:
    context_items = normalize_context_to_list(context_text)
    prompt = build_structured_prompt(question, context_items)

    if DEBUG_PROMPTS:
        header = "\n=== PROMPT START ===\n"
        footer = "\n=== PROMPT END ===\n"
        if PROMPT_LOG:
            with open(PROMPT_LOG, "a", encoding=ENCODING) as f:
                f.write(header + prompt + footer)
        else:
            print(header + prompt + footer)

    inputs = tokenizer(prompt, return_tensors="pt").to(model.device)
    output_ids = model.generate(
        **inputs,
        max_new_tokens=MAX_NEW_TOKENS,
        do_sample=False,
        pad_token_id=tokenizer.eos_token_id if tokenizer.eos_token_id is not None else tokenizer.pad_token_id,
    )
    gen_ids = output_ids[0, inputs.input_ids.shape[1]:]
    text = tokenizer.decode(gen_ids, skip_special_tokens=True).strip()
    return text

# ---------- Incremental CSV writing using csv module ----------
def ensure_header(out_path: str, header_cols: List[str]):
    """
    Create CSV with header if it doesn't exist or is empty.
    """
    need_header = (not os.path.exists(out_path)) or (os.path.getsize(out_path) == 0)
    if need_header:
        os.makedirs(os.path.dirname(out_path), exist_ok=True)
        with open(out_path, "w", encoding=ENCODING, newline=NEWLINE) as f:
            writer = csv.writer(f)
            writer.writerow(header_cols)

def append_row(out_path: str, row_values: Iterable[Any]):
    """
    Append a single row to the CSV and fsync to ensure durability.
    row_values must match the header column order.
    """
    with open(out_path, "a", encoding=ENCODING, newline=NEWLINE) as f:
        writer = csv.writer(f)
        writer.writerow(row_values)
        f.flush()
        os.fsync(f.fileno())

def run_inference_for_column_incremental(
    df: pd.DataFrame,
    ctx_col: str,
    out_col: str,
    out_path: str,
    source_label: str,
):
    header_cols = list(df.columns) + [out_col]
    ensure_header(out_path, header_cols)

    for idx, row in df.iterrows():
        question = row.get(QUESTION_COL, "")
        context_text = row.get(ctx_col, "")

        if DEBUG_PROMPTS and not PROMPT_LOG:
            preview_q = str(question)[:120].replace("\n", " ")
            print(f"\n--- Row {idx} | Source: {source_label} | Question: {preview_q} ---")

        try:
            ans = generate_answer(question, context_text)
        except Exception as e:
            ans = f"[ERROR DURING GENERATION: {e}]"

        # Compose values in the header order
        row_values = [row.get(c, "") for c in df.columns] + [ans]
        append_row(out_path, row_values)

def main():
    df = pd.read_csv(INPUT_CSV)

    required = [QUESTION_COL, HYBRID_CTX_COL, CONTRIEVER_CTX_COL]
    missing = [c for c in required if c not in df.columns]
    if missing:
        raise ValueError(f"Missing required column(s) in CSV: {missing}")

    if TEST_LIMIT is not None:
        df = df.head(TEST_LIMIT)

    # 1) HYBRID pass
    out_hybrid = "output_files/halubench/halubench_answers_hybrid_qwen3_4b_1200rows.csv" if TEST_LIMIT else OUTPUT_HYBRID_CSV
    run_inference_for_column_incremental(
        df.copy(),
        ctx_col=HYBRID_CTX_COL,
        out_col="answer_gemma2b_hybrid",
        out_path=out_hybrid,
        source_label="hybrid_full_text"
    )
    print(f"Wrote incrementally: {out_hybrid}")

    # 2) CONTRIEVER pass
    out_contr = "output_files/halubench/halubench_answers_contriever_qwen3_4b_1200rows.csv" if TEST_LIMIT else OUTPUT_CONTRIEVER_CSV
    run_inference_for_column_incremental(
        df.copy(),
        ctx_col=CONTRIEVER_CTX_COL,
        out_col="answer_gemma2b_contriever",
        out_path=out_contr,
        source_label="contriever_full_text"
    )
    print(f"Wrote incrementally: {out_contr}")

if __name__ == "__main__":
    main()

In [ ]:
# Staring from where it stopped the generation berore, at row 735

import os
import json
import csv
import pandas as pd
import torch
from typing import List, Optional, Any, Iterable
from transformers import AutoModelForCausalLM, AutoTokenizer

# ========= CONFIG =========
INPUT_CSV = 'output_files/halubench/halubench_combined_results_with_1200_full_texts.csv'  # must contain: question, hybrid_full_text, contriever_full_text
OUTPUT_HYBRID_CSV = "output_files/halubench/halubench_answers_hybrid_qwen3_4b_1200rows.csv"
OUTPUT_CONTRIEVER_CSV = "output_files/halubench/halubench_answers_contriever_qwen3_4b_1200rows.csv"

# Only process first N rows when testing. Set to None to process all.
TEST_LIMIT: Optional[int] = None  # set None for full run

# Start processing from this row number (0-indexed)
START_ROW: int = 878

QUESTION_COL = "question"
HYBRID_CTX_COL = "hybrid_full_text"
CONTRIEVER_CTX_COL = "contriever_full_text"

# MODEL: switched to Qwen 3 4B Instruct
MODEL_ID = "Qwen/Qwen3-4B-Instruct-2507"
DEVICE = "cuda" if torch.cuda.is_available() else "cpu"

# Inference/runtime knobs
MAX_NEW_TOKENS = 256
SEED = 42

# Debug: print the exact prompt fed to the model
DEBUG_PROMPTS = True
PROMPT_LOG = None  # e.g., "prompt_log.txt" to save to file; keep None to print to stdout

# Optional: clip long context to avoid OOM
MAX_CTX_CHARS_PER_ITEM = 2000  # clip each item; adjust as needed

# If your context columns are delimiter-separated strings (not JSON), set a delimiter here.
# If None, we will try JSON first; if that fails, treat the whole cell as one item.
CONTEXT_SPLIT_DELIM: Optional[str] = None  # e.g., " ||| " or "\n\n"

ENCODING = "utf-8"
NEWLINE = ""  # important for csv on Windows

torch.manual_seed(SEED)
# ==========================

# ---------- Load model + tokenizer ----------
tokenizer = AutoTokenizer.from_pretrained(MODEL_ID, use_fast=True)
# Ensure pad token exists (common for Qwen)
if tokenizer.pad_token_id is None and tokenizer.eos_token_id is not None:
    tokenizer.pad_token = tokenizer.eos_token

model = AutoModelForCausalLM.from_pretrained(
    MODEL_ID,
    torch_dtype=torch.float16 if torch.cuda.is_available() else torch.float16,
    device_map="auto"  # may offload to CPU if VRAM insufficient
)
if DEVICE != "cuda":
    model.to(DEVICE)

# ---------- Helpers to normalize context into a list of items ----------
def normalize_context_to_list(val: Any) -> List[str]:
    """
    Converts the cell value into a list of strings (context items).
    Accepts:
      - JSON array of strings
      - JSON array of dicts with "full_text" (will extract the strings)
      - Delimiter-separated string if CONTEXT_SPLIT_DELIM is set
      - Plain string (returns [string])
      - list[str]
      - list[dict] with "full_text"
    """
    if val is None or (isinstance(val, float) and pd.isna(val)):
        return []

    if isinstance(val, list):
        items = []
        for item in val:
            if isinstance(item, dict):
                if "full_text" in item and isinstance(item["full_text"], str):
                    items.append(item["full_text"])
            elif isinstance(item, str):
                items.append(item)
        return [s for s in items if s and str(s).strip()]

    if isinstance(val, dict):
        for k in ["docs", "results", "items", "data"]:
            if k in val and isinstance(val[k], list):
                return normalize_context_to_list(val[k])
        if "full_text" in val and isinstance(val["full_text"], str):
            return [val["full_text"]]
        return []

    if isinstance(val, str):
        s = val.strip()
        if s.startswith("[") or s.startswith("{"):
            try:
                parsed = json.loads(s)
                return normalize_context_to_list(parsed)
            except Exception:
                pass
        if CONTEXT_SPLIT_DELIM is not None and CONTEXT_SPLIT_DELIM in s:
            parts = [p.strip() for p in s.split(CONTEXT_SPLIT_DELIM)]
            return [p for p in parts if p]
        return [s]

    return [str(val)]

# ---------- Structured Prompt builder ----------
def build_structured_prompt(question: str, context_items: List[str]) -> str:
    labeled_lines = []
    for i, txt in enumerate(context_items, start=1):
        tx = str(txt)
        if MAX_CTX_CHARS_PER_ITEM is not None:
            tx = tx[:MAX_CTX_CHARS_PER_ITEM]
        clean = " ".join(tx.split())
        labeled_lines.append(f"[context {i}] - {clean}")
    contexts_block = "\n".join(labeled_lines) if labeled_lines else ""

    prompt = (
        "You are a helpful assistant. Follow the user's instructions carefully and answer the question in one or max two sentences. "
        "Do not repeat any part of the prompt in your final answer and answer strictly based on provided contexts.\n\n"
        "Prompt:\n"
        f"Question:- {question}\n"
        "Contexts:-\n"
        f"{contexts_block}\n\n"
        "Your task is to answer the given question by thinking progressively following the steps:\n"
        "Step 0: Process the answer within your memory and only provide the necessary answer.\n"
        "Step 1: Carefully read and understand the question and given contexts which can support you to answer better.\n"
        "Step 2: Analyze whether the given contexts provides sufficient information to answer the question.\n"
        "- If the given contexts do not provide sufficient information, respond with: 'The context does not provide sufficient information to answer the question.'\n"
        "- If the given contexts provide sufficient information, proceed to Step 3.\n"
        "Step 3: Generate an accurate and grounded response strictly based on the provided contexts. Avoid guessing or providing incorrect/hallucinated responses.\n"
        "Step 4: Only when you are sure of Step 3, Clearly state the final answer in one or two sentences.\n\n"
        "Answer:"
    )
    return prompt

def generate_answer(question: str, context_text: Any) -> str:
    context_items = normalize_context_to_list(context_text)
    prompt = build_structured_prompt(question, context_items)

    if DEBUG_PROMPTS:
        header = "\n=== PROMPT START ===\n"
        footer = "\n=== PROMPT END ===\n"
        if PROMPT_LOG:
            with open(PROMPT_LOG, "a", encoding=ENCODING) as f:
                f.write(header + prompt + footer)
        else:
            print(header + prompt + footer)

    inputs = tokenizer(prompt, return_tensors="pt").to(model.device)
    output_ids = model.generate(
        **inputs,
        max_new_tokens=MAX_NEW_TOKENS,
        do_sample=False,
        pad_token_id=tokenizer.eos_token_id if tokenizer.eos_token_id is not None else tokenizer.pad_token_id,
    )
    gen_ids = output_ids[0, inputs.input_ids.shape[1]:]
    text = tokenizer.decode(gen_ids, skip_special_tokens=True).strip()
    return text

# ---------- Incremental CSV writing using csv module ----------
def ensure_header(out_path: str, header_cols: List[str]):
    """
    Create CSV with header if it doesn't exist or is empty.
    """
    need_header = (not os.path.exists(out_path)) or (os.path.getsize(out_path) == 0)
    if need_header:
        os.makedirs(os.path.dirname(out_path), exist_ok=True)
        with open(out_path, "w", encoding=ENCODING, newline=NEWLINE) as f:
            writer = csv.writer(f)
            writer.writerow(header_cols)

def append_row(out_path: str, row_values: Iterable[Any]):
    """
    Append a single row to the CSV and fsync to ensure durability.
    row_values must match the header column order.
    """
    with open(out_path, "a", encoding=ENCODING, newline=NEWLINE) as f:
        writer = csv.writer(f)
        writer.writerow(row_values)
        f.flush()
        os.fsync(f.fileno())

def run_inference_for_column_incremental(
    df: pd.DataFrame,
    ctx_col: str,
    out_col: str,
    out_path: str,
    source_label: str,
    start_row: int = 0,
):
    header_cols = list(df.columns) + [out_col]
    ensure_header(out_path, header_cols)

    for idx, row in df.iterrows():
        # Skip rows before start_row
        if idx < start_row:
            continue
            
        question = row.get(QUESTION_COL, "")
        context_text = row.get(ctx_col, "")

        if DEBUG_PROMPTS and not PROMPT_LOG:
            preview_q = str(question)[:120].replace("\n", " ")
            print(f"\n--- Row {idx} | Source: {source_label} | Question: {preview_q} ---")

        try:
            ans = generate_answer(question, context_text)
        except Exception as e:
            ans = f"[ERROR DURING GENERATION: {e}]"

        # Compose values in the header order
        row_values = [row.get(c, "") for c in df.columns] + [ans]
        append_row(out_path, row_values)

def main():
    df = pd.read_csv(INPUT_CSV)

    required = [QUESTION_COL, HYBRID_CTX_COL, CONTRIEVER_CTX_COL]
    missing = [c for c in required if c not in df.columns]
    if missing:
        raise ValueError(f"Missing required column(s) in CSV: {missing}")

    if TEST_LIMIT is not None:
        df = df.head(TEST_LIMIT)

    # 1) HYBRID pass - COMMENTED OUT
    # out_hybrid = "output_files/halubench/halubench_answers_hybrid_qwen3_4b_1200rows.csv" if TEST_LIMIT else OUTPUT_HYBRID_CSV
    # run_inference_for_column_incremental(
    #     df.copy(),
    #     ctx_col=HYBRID_CTX_COL,
    #     out_col="answer_gemma2b_hybrid",
    #     out_path=out_hybrid,
    #     source_label="hybrid_full_text"
    # )
    # print(f"Wrote incrementally: {out_hybrid}")

    # 2) CONTRIEVER pass - Starting from row 878
    out_contr = "output_files/halubench/halubench_answers_contriever_qwen3_4b_1200rows.csv" if TEST_LIMIT else OUTPUT_CONTRIEVER_CSV
    run_inference_for_column_incremental(
        df.copy(),
        ctx_col=CONTRIEVER_CTX_COL,
        out_col="answer_gemma2b_contriever",
        out_path=out_contr,
        source_label="contriever_full_text",
        start_row=START_ROW
    )
    print(f"Wrote incrementally: {out_contr}")

if __name__ == "__main__":
    main()

## Qwen on hotpot 1200

In [1]:
import os
import json
import csv
import pandas as pd
import torch
from typing import List, Optional, Any, Iterable
from transformers import AutoModelForCausalLM, AutoTokenizer

# ========= CONFIG =========
INPUT_CSV = 'output_files/hotpot/hotpotqa_sampled_with_full_texts_1200.csv'  # must contain: question, hybrid_full_text, contriever_full_text
OUTPUT_HYBRID_CSV = "output_files/hotpot/hotpotqa_answers_hybrid_qwen3_4b_1200rows.csv"
OUTPUT_CONTRIEVER_CSV = "output_files/hotpot/hotpotqa_answers_contriever_qwen3_4b_1200rows.csv"

# Only process first N rows when testing. Set to None to process all.
TEST_LIMIT: Optional[int] = None  # set None for full run

QUESTION_COL = "question"
HYBRID_CTX_COL = "hybrid_full_text"
CONTRIEVER_CTX_COL = "contriever_full_text"

# MODEL: switched to Qwen 3 4B Instruct
MODEL_ID = "Qwen/Qwen3-4B-Instruct-2507"
DEVICE = "cuda" if torch.cuda.is_available() else "cpu"

# Inference/runtime knobs
MAX_NEW_TOKENS = 256
SEED = 42

# Debug: print the exact prompt fed to the model
DEBUG_PROMPTS = True
PROMPT_LOG = None  # e.g., "prompt_log.txt" to save to file; keep None to print to stdout

# Optional: clip long context to avoid OOM
MAX_CTX_CHARS_PER_ITEM = 2000  # clip each item; adjust as needed

# If your context columns are delimiter-separated strings (not JSON), set a delimiter here.
# If None, we will try JSON first; if that fails, treat the whole cell as one item.
CONTEXT_SPLIT_DELIM: Optional[str] = None  # e.g., " ||| " or "\n\n"

ENCODING = "utf-8"
NEWLINE = ""  # important for csv on Windows

torch.manual_seed(SEED)
# ==========================

# ---------- Load model + tokenizer ----------
tokenizer = AutoTokenizer.from_pretrained(MODEL_ID, use_fast=True)
# Ensure pad token exists (common for Qwen)
if tokenizer.pad_token_id is None and tokenizer.eos_token_id is not None:
    tokenizer.pad_token = tokenizer.eos_token

model = AutoModelForCausalLM.from_pretrained(
    MODEL_ID,
    torch_dtype=torch.float16 if torch.cuda.is_available() else torch.float16,
    device_map="auto"  # may offload to CPU if VRAM insufficient
)
if DEVICE != "cuda":
    model.to(DEVICE)

# ---------- Helpers to normalize context into a list of items ----------
def normalize_context_to_list(val: Any) -> List[str]:
    """
    Converts the cell value into a list of strings (context items).
    Accepts:
      - JSON array of strings
      - JSON array of dicts with "full_text" (will extract the strings)
      - Delimiter-separated string if CONTEXT_SPLIT_DELIM is set
      - Plain string (returns [string])
      - list[str]
      - list[dict] with "full_text"
    """
    if val is None or (isinstance(val, float) and pd.isna(val)):
        return []

    if isinstance(val, list):
        items = []
        for item in val:
            if isinstance(item, dict):
                if "full_text" in item and isinstance(item["full_text"], str):
                    items.append(item["full_text"])
            elif isinstance(item, str):
                items.append(item)
        return [s for s in items if s and str(s).strip()]

    if isinstance(val, dict):
        for k in ["docs", "results", "items", "data"]:
            if k in val and isinstance(val[k], list):
                return normalize_context_to_list(val[k])
        if "full_text" in val and isinstance(val["full_text"], str):
            return [val["full_text"]]
        return []

    if isinstance(val, str):
        s = val.strip()
        if s.startswith("[") or s.startswith("{"):
            try:
                parsed = json.loads(s)
                return normalize_context_to_list(parsed)
            except Exception:
                pass
        if CONTEXT_SPLIT_DELIM is not None and CONTEXT_SPLIT_DELIM in s:
            parts = [p.strip() for p in s.split(CONTEXT_SPLIT_DELIM)]
            return [p for p in parts if p]
        return [s]

    return [str(val)]

# ---------- Structured Prompt builder ----------
def build_structured_prompt(question: str, context_items: List[str]) -> str:
    labeled_lines = []
    for i, txt in enumerate(context_items, start=1):
        tx = str(txt)
        if MAX_CTX_CHARS_PER_ITEM is not None:
            tx = tx[:MAX_CTX_CHARS_PER_ITEM]
        clean = " ".join(tx.split())
        labeled_lines.append(f"[context {i}] - {clean}")
    contexts_block = "\n".join(labeled_lines) if labeled_lines else ""

    prompt = (
        "You are a helpful assistant. Follow the user's instructions carefully and answer the question in one or max two sentences. "
        "Do not repeat any part of the prompt in your final answer and answer strictly based on provided contexts.\n\n"
        "Prompt:\n"
        f"Question:- {question}\n"
        "Contexts:-\n"
        f"{contexts_block}\n\n"
        "Your task is to answer the given question by thinking progressively following the steps:\n"
        "Step 0: Process the answer within your memory and only provide the necessary answer.\n"
        "Step 1: Carefully read and understand the question and given contexts which can support you to answer better.\n"
        "Step 2: Analyze whether the given contexts provides sufficient information to answer the question.\n"
        "- If the given contexts do not provide sufficient information, respond with: “The context does not provide sufficient information to answer the question.”\n"
        "- If the given contexts provide sufficient information, proceed to Step 3.\n"
        "Step 3: Generate an accurate and grounded response strictly based on the provided contexts. Avoid guessing or providing incorrect/hallucinated responses.\n"
        "Step 4: Only when you are sure of Step 3, Clearly state the final answer in one or two sentences.\n\n"
        "Answer:"
    )
    return prompt

def generate_answer(question: str, context_text: Any) -> str:
    context_items = normalize_context_to_list(context_text)
    prompt = build_structured_prompt(question, context_items)

    if DEBUG_PROMPTS:
        header = "\n=== PROMPT START ===\n"
        footer = "\n=== PROMPT END ===\n"
        if PROMPT_LOG:
            with open(PROMPT_LOG, "a", encoding=ENCODING) as f:
                f.write(header + prompt + footer)
        else:
            print(header + prompt + footer)

    inputs = tokenizer(prompt, return_tensors="pt").to(model.device)
    output_ids = model.generate(
        **inputs,
        max_new_tokens=MAX_NEW_TOKENS,
        do_sample=False,
        pad_token_id=tokenizer.eos_token_id if tokenizer.eos_token_id is not None else tokenizer.pad_token_id,
    )
    gen_ids = output_ids[0, inputs.input_ids.shape[1]:]
    text = tokenizer.decode(gen_ids, skip_special_tokens=True).strip()
    return text

# ---------- Incremental CSV writing using csv module ----------
def ensure_header(out_path: str, header_cols: List[str]):
    """
    Create CSV with header if it doesn't exist or is empty.
    """
    need_header = (not os.path.exists(out_path)) or (os.path.getsize(out_path) == 0)
    if need_header:
        os.makedirs(os.path.dirname(out_path), exist_ok=True)
        with open(out_path, "w", encoding=ENCODING, newline=NEWLINE) as f:
            writer = csv.writer(f)
            writer.writerow(header_cols)

def append_row(out_path: str, row_values: Iterable[Any]):
    """
    Append a single row to the CSV and fsync to ensure durability.
    row_values must match the header column order.
    """
    with open(out_path, "a", encoding=ENCODING, newline=NEWLINE) as f:
        writer = csv.writer(f)
        writer.writerow(row_values)
        f.flush()
        os.fsync(f.fileno())

def run_inference_for_column_incremental(
    df: pd.DataFrame,
    ctx_col: str,
    out_col: str,
    out_path: str,
    source_label: str,
):
    header_cols = list(df.columns) + [out_col]
    ensure_header(out_path, header_cols)

    for idx, row in df.iterrows():
        question = row.get(QUESTION_COL, "")
        context_text = row.get(ctx_col, "")

        if DEBUG_PROMPTS and not PROMPT_LOG:
            preview_q = str(question)[:120].replace("\n", " ")
            print(f"\n--- Row {idx} | Source: {source_label} | Question: {preview_q} ---")

        try:
            ans = generate_answer(question, context_text)
        except Exception as e:
            ans = f"[ERROR DURING GENERATION: {e}]"

        # Compose values in the header order
        row_values = [row.get(c, "") for c in df.columns] + [ans]
        append_row(out_path, row_values)

def main():
    df = pd.read_csv(INPUT_CSV)

    required = [QUESTION_COL, HYBRID_CTX_COL, CONTRIEVER_CTX_COL]
    missing = [c for c in required if c not in df.columns]
    if missing:
        raise ValueError(f"Missing required column(s) in CSV: {missing}")

    if TEST_LIMIT is not None:
        df = df.head(TEST_LIMIT)

    # 1) HYBRID pass
    out_hybrid = "output_files/hotpot/hotpotqa_answers_hybrid_qwen3_4b_1200rows.csv" if TEST_LIMIT else OUTPUT_HYBRID_CSV
    run_inference_for_column_incremental(
        df.copy(),
        ctx_col=HYBRID_CTX_COL,
        out_col="answer_gemma2b_hybrid",
        out_path=out_hybrid,
        source_label="hybrid_full_text"
    )
    print(f"Wrote incrementally: {out_hybrid}")

    # 2) CONTRIEVER pass
    out_contr = "output_files/hotpot/hotpotqa_answers_contriever_qwen3_4b_1200rows.csv" if TEST_LIMIT else OUTPUT_CONTRIEVER_CSV
    run_inference_for_column_incremental(
        df.copy(),
        ctx_col=CONTRIEVER_CTX_COL,
        out_col="answer_gemma2b_contriever",
        out_path=out_contr,
        source_label="contriever_full_text"
    )
    print(f"Wrote incrementally: {out_contr}")

if __name__ == "__main__":
    main()

/home/csmala/miniconda3/envs/uncertainity/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Loading checkpoint shards: 100%|██████████| 3/3 [00:02<00:00,  1.30it/s]
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



--- Row 0 | Source: hybrid_full_text | Question: Who was the widow affected by the Same-sex marriage decision ruled on by the Sixth Circuit from Ohio? ---

=== PROMPT START ===
You are a helpful assistant. Follow the user's instructions carefully and answer the question in one or max two sentences. Do not repeat any part of the prompt in your final answer and answer strictly based on provided contexts.

Prompt:
Question:- Who was the widow affected by the Same-sex marriage decision ruled on by the Sixth Circuit from Ohio?
Contexts:-
[context 1] - on april 28, 2015, the supreme court of the united states heard oral arguments for obergefell v. hodges (ohio), which was consolidated with three other same-sex marriage cases from the other states in the sixth circuit: tanco v. haslam (tennessee), deboer v. snyder (michigan), bourke v. beshear (kentucky).
[context 2] - same-sex marriage in ohio is legal under the u.s. supreme court ruling in obergefell v. hodges, a landmark decision in which

The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



--- Row 1 | Source: hybrid_full_text | Question: Rowland Barnes was murdered by a man on trial for what crime? ---

=== PROMPT START ===
You are a helpful assistant. Follow the user's instructions carefully and answer the question in one or max two sentences. Do not repeat any part of the prompt in your final answer and answer strictly based on provided contexts.

Prompt:
Question:- Rowland Barnes was murdered by a man on trial for what crime?
Contexts:-
[context 1] - rowland w. barnes (april 25, 1940 – march 11, 2005) was a fulton county, georgia, united states, superior court judge.
[context 2] - judge barnes was shot to death in his courtroom by brian nichols in 2005.
[context 3] - at his trial, he was found guilty of murder and sentenced to death; this sentence was later reduced to life imprisonment.
[context 4] - after eight days of deliberations, a jury convicted him of first-degree murder on december 23, 2014.
[context 5] - nichols was on trial for rape when he escaped from cus

The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.


...


--- Row 652 | Source: hybrid_full_text | Question: Who was born first, Dan Brown or Henry Roth? ---

=== PROMPT START ===
You are a helpful assistant. Follow the user's instructions carefully and answer the question in one or max two sentences. Do not repeat any part of the prompt in your final answer and answer strictly based on provided contexts.

Prompt:
Question:- Who was born first, Dan Brown or Henry Roth?
Contexts:-
[context 1] - henry roth (february 8, 1906 – october 13, 1995) was an american novelist and short story writer.
[context 2] - daniel gerhard dan brown (born june 22, 1964) is an american author of thriller fiction, most notably the novels angels & demons (2000), the da vinci code (2003), and inferno (2013).
[context 3] - henry box brown (c. 1816 – june 15, 1897) was a 19th-century virginia slave who escaped to freedom at the age of 33 by arranging to have himself mailed in a wooden crate in 1849 to abolitionists in philadelphia, pennsylvania.
[context 4] - henry new

The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



--- Row 653 | Source: hybrid_full_text | Question: Subgenre of heavy metal, Neoclassical metal, was pioneered by an English rock band formed in Hertford in what year? ---

=== PROMPT START ===
You are a helpful assistant. Follow the user's instructions carefully and answer the question in one or max two sentences. Do not repeat any part of the prompt in your final answer and answer strictly based on provided contexts.

Prompt:
Question:- Subgenre of heavy metal, Neoclassical metal, was pioneered by an English rock band formed in Hertford in what year?
Contexts:-
[context 1] - deep purple are an english rock band formed in hertford in 1968.
[context 2] - the band are often considered a precursor to the new wave of british heavy metal, which re-energised heavy metal in the late 1970s and early 1980s.
[context 3] - neoclassical metal is a subgenre of heavy metal that is heavily influenced by classical music and usually features very technical playing, consisting of elements borrowed from

The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



--- Row 654 | Source: hybrid_full_text | Question: What does University of Alabama at Birmingham and University of Kansas have in common? ---

=== PROMPT START ===
You are a helpful assistant. Follow the user's instructions carefully and answer the question in one or max two sentences. Do not repeat any part of the prompt in your final answer and answer strictly based on provided contexts.

Prompt:
Question:- What does University of Alabama at Birmingham and University of Kansas have in common?
Contexts:-
[context 1] - the university of alabama at birmingham (uab) is a public research university in birmingham in the u.s. state of alabama.
[context 2] - the university of alabama (alabama or ua) is a public research university located in tuscaloosa, alabama, united states, and the flagship of the university of alabama system.
[context 3] - the university of alabama in huntsville (also known as uahuntsville or uah) is a state-supported, public, coeducational research university in huntsv

In [1]:
# Re Start from row 35 where it was stopped before

import os
import json
import csv
import pandas as pd
import torch
from typing import List, Optional, Any, Iterable
from transformers import AutoModelForCausalLM, AutoTokenizer

# ========= CONFIG =========
INPUT_CSV = 'output_files/hotpot/hotpotqa_sampled_with_full_texts_1200.csv'  # must contain: question, hybrid_full_text, contriever_full_text
OUTPUT_HYBRID_CSV = "output_files/hotpot/hotpotqa_answers_hybrid_qwen3_4b_1200rows.csv"
OUTPUT_CONTRIEVER_CSV = "output_files/hotpot/hotpotqa_answers_contriever_qwen3_4b_1200rows.csv"

# Only process first N rows when testing. Set to None to process all.
TEST_LIMIT: Optional[int] = None  # set None for full run

# Start processing from this row number (0-indexed)
START_ROW: int = 215

QUESTION_COL = "question"
HYBRID_CTX_COL = "hybrid_full_text"
CONTRIEVER_CTX_COL = "contriever_full_text"

# MODEL: switched to Qwen 3 4B Instruct
MODEL_ID = "Qwen/Qwen3-4B-Instruct-2507"
DEVICE = "cuda" if torch.cuda.is_available() else "cpu"

# Inference/runtime knobs
MAX_NEW_TOKENS = 256
SEED = 42

# Debug: print the exact prompt fed to the model
DEBUG_PROMPTS = True
PROMPT_LOG = None  # e.g., "prompt_log.txt" to save to file; keep None to print to stdout

# Optional: clip long context to avoid OOM
MAX_CTX_CHARS_PER_ITEM = 2000  # clip each item; adjust as needed

# If your context columns are delimiter-separated strings (not JSON), set a delimiter here.
# If None, we will try JSON first; if that fails, treat the whole cell as one item.
CONTEXT_SPLIT_DELIM: Optional[str] = None  # e.g., " ||| " or "\n\n"

ENCODING = "utf-8"
NEWLINE = ""  # important for csv on Windows

torch.manual_seed(SEED)
# ==========================

# ---------- Load model + tokenizer ----------
tokenizer = AutoTokenizer.from_pretrained(MODEL_ID, use_fast=True)
# Ensure pad token exists (common for Qwen)
if tokenizer.pad_token_id is None and tokenizer.eos_token_id is not None:
    tokenizer.pad_token = tokenizer.eos_token

model = AutoModelForCausalLM.from_pretrained(
    MODEL_ID,
    torch_dtype=torch.float16 if torch.cuda.is_available() else torch.float16,
    device_map="auto"  # may offload to CPU if VRAM insufficient
)
if DEVICE != "cuda":
    model.to(DEVICE)

# ---------- Helpers to normalize context into a list of items ----------
def normalize_context_to_list(val: Any) -> List[str]:
    """
    Converts the cell value into a list of strings (context items).
    Accepts:
      - JSON array of strings
      - JSON array of dicts with "full_text" (will extract the strings)
      - Delimiter-separated string if CONTEXT_SPLIT_DELIM is set
      - Plain string (returns [string])
      - list[str]
      - list[dict] with "full_text"
    """
    if val is None or (isinstance(val, float) and pd.isna(val)):
        return []

    if isinstance(val, list):
        items = []
        for item in val:
            if isinstance(item, dict):
                if "full_text" in item and isinstance(item["full_text"], str):
                    items.append(item["full_text"])
            elif isinstance(item, str):
                items.append(item)
        return [s for s in items if s and str(s).strip()]

    if isinstance(val, dict):
        for k in ["docs", "results", "items", "data"]:
            if k in val and isinstance(val[k], list):
                return normalize_context_to_list(val[k])
        if "full_text" in val and isinstance(val["full_text"], str):
            return [val["full_text"]]
        return []

    if isinstance(val, str):
        s = val.strip()
        if s.startswith("[") or s.startswith("{"):
            try:
                parsed = json.loads(s)
                return normalize_context_to_list(parsed)
            except Exception:
                pass
        if CONTEXT_SPLIT_DELIM is not None and CONTEXT_SPLIT_DELIM in s:
            parts = [p.strip() for p in s.split(CONTEXT_SPLIT_DELIM)]
            return [p for p in parts if p]
        return [s]

    return [str(val)]

# ---------- Structured Prompt builder ----------
def build_structured_prompt(question: str, context_items: List[str]) -> str:
    labeled_lines = []
    for i, txt in enumerate(context_items, start=1):
        tx = str(txt)
        if MAX_CTX_CHARS_PER_ITEM is not None:
            tx = tx[:MAX_CTX_CHARS_PER_ITEM]
        clean = " ".join(tx.split())
        labeled_lines.append(f"[context {i}] - {clean}")
    contexts_block = "\n".join(labeled_lines) if labeled_lines else ""

    prompt = (
        "You are a helpful assistant. Follow the user's instructions carefully and answer the question in one or max two sentences. "
        "Do not repeat any part of the prompt in your final answer and answer strictly based on provided contexts.\n\n"
        "Prompt:\n"
        f"Question:- {question}\n"
        "Contexts:-\n"
        f"{contexts_block}\n\n"
        "Your task is to answer the given question by thinking progressively following the steps:\n"
        "Step 0: Process the answer within your memory and only provide the necessary answer.\n"
        "Step 1: Carefully read and understand the question and given contexts which can support you to answer better.\n"
        "Step 2: Analyze whether the given contexts provides sufficient information to answer the question.\n"
        "- If the given contexts do not provide sufficient information, respond with: 'The context does not provide sufficient information to answer the question.'\n"
        "- If the given contexts provide sufficient information, proceed to Step 3.\n"
        "Step 3: Generate an accurate and grounded response strictly based on the provided contexts. Avoid guessing or providing incorrect/hallucinated responses.\n"
        "Step 4: Only when you are sure of Step 3, Clearly state the final answer in one or two sentences.\n\n"
        "Answer:"
    )
    return prompt

def generate_answer(question: str, context_text: Any) -> str:
    context_items = normalize_context_to_list(context_text)
    prompt = build_structured_prompt(question, context_items)

    if DEBUG_PROMPTS:
        header = "\n=== PROMPT START ===\n"
        footer = "\n=== PROMPT END ===\n"
        if PROMPT_LOG:
            with open(PROMPT_LOG, "a", encoding=ENCODING) as f:
                f.write(header + prompt + footer)
        else:
            print(header + prompt + footer)

    inputs = tokenizer(prompt, return_tensors="pt").to(model.device)
    output_ids = model.generate(
        **inputs,
        max_new_tokens=MAX_NEW_TOKENS,
        do_sample=False,
        pad_token_id=tokenizer.eos_token_id if tokenizer.eos_token_id is not None else tokenizer.pad_token_id,
    )
    gen_ids = output_ids[0, inputs.input_ids.shape[1]:]
    text = tokenizer.decode(gen_ids, skip_special_tokens=True).strip()
    return text

# ---------- Incremental CSV writing using csv module ----------
def ensure_header(out_path: str, header_cols: List[str]):
    """
    Create CSV with header if it doesn't exist or is empty.
    """
    need_header = (not os.path.exists(out_path)) or (os.path.getsize(out_path) == 0)
    if need_header:
        os.makedirs(os.path.dirname(out_path), exist_ok=True)
        with open(out_path, "w", encoding=ENCODING, newline=NEWLINE) as f:
            writer = csv.writer(f)
            writer.writerow(header_cols)

def append_row(out_path: str, row_values: Iterable[Any]):
    """
    Append a single row to the CSV and fsync to ensure durability.
    row_values must match the header column order.
    """
    with open(out_path, "a", encoding=ENCODING, newline=NEWLINE) as f:
        writer = csv.writer(f)
        writer.writerow(row_values)
        f.flush()
        os.fsync(f.fileno())

def run_inference_for_column_incremental(
    df: pd.DataFrame,
    ctx_col: str,
    out_col: str,
    out_path: str,
    source_label: str,
    start_row: int = 0,
):
    header_cols = list(df.columns) + [out_col]
    ensure_header(out_path, header_cols)

    for idx, row in df.iterrows():
        # Skip rows before start_row
        if idx < start_row:
            continue
            
        question = row.get(QUESTION_COL, "")
        context_text = row.get(ctx_col, "")

        if DEBUG_PROMPTS and not PROMPT_LOG:
            preview_q = str(question)[:120].replace("\n", " ")
            print(f"\n--- Row {idx} | Source: {source_label} | Question: {preview_q} ---")

        try:
            ans = generate_answer(question, context_text)
        except Exception as e:
            ans = f"[ERROR DURING GENERATION: {e}]"

        # Compose values in the header order
        row_values = [row.get(c, "") for c in df.columns] + [ans]
        append_row(out_path, row_values)

def main():
    df = pd.read_csv(INPUT_CSV)

    required = [QUESTION_COL, HYBRID_CTX_COL, CONTRIEVER_CTX_COL]
    missing = [c for c in required if c not in df.columns]
    if missing:
        raise ValueError(f"Missing required column(s) in CSV: {missing}")

    if TEST_LIMIT is not None:
        df = df.head(TEST_LIMIT)

    # 1) HYBRID pass - COMMENTED OUT
    # out_hybrid = "output_files/hotpot/hotpotqa_answers_hybrid_qwen3_4b_1200rows.csv" if TEST_LIMIT else OUTPUT_HYBRID_CSV
    # run_inference_for_column_incremental(
    #     df.copy(),
    #     ctx_col=HYBRID_CTX_COL,
    #     out_col="answer_gemma2b_hybrid",
    #     out_path=out_hybrid,
    #     source_label="hybrid_full_text"
    # )
    # print(f"Wrote incrementally: {out_hybrid}")

    # 2) CONTRIEVER pass - Starting from row 215
    out_contr = "output_files/hotpot/hotpotqa_answers_contriever_qwen3_4b_1200rows.csv" if TEST_LIMIT else OUTPUT_CONTRIEVER_CSV
    run_inference_for_column_incremental(
        df.copy(),
        ctx_col=CONTRIEVER_CTX_COL,
        out_col="answer_gemma2b_contriever",
        out_path=out_contr,
        source_label="contriever_full_text",
        start_row=START_ROW
    )
    print(f"Wrote incrementally: {out_contr}")

if __name__ == "__main__":
    main()

/home/csmala/miniconda3/envs/uncertainity/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Loading checkpoint shards: 100%|██████████| 3/3 [00:01<00:00,  1.64it/s]
The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



--- Row 215 | Source: contriever_full_text | Question: In what year was the school at which Simon Brown was Head of Academic and Choral Music for 12 years awarded the UNESCO M ---

=== PROMPT START ===
You are a helpful assistant. Follow the user's instructions carefully and answer the question in one or max two sentences. Do not repeat any part of the prompt in your final answer and answer strictly based on provided contexts.

Prompt:
Question:- In what year was the school at which Simon Brown was Head of Academic and Choral Music for 12 years awarded the UNESCO Mozart Medal?
Contexts:-
[context 1] - simon brown was the director of music at king's college school in cambridge from 1999-2014.
[context 2] - sir simon rattle is honorary president of the school.
[context 3] - his teaching career began at bradford grammar school in yorkshire, and was followed by 12 years as head of academic and choral music at the purcell school.
[context 4] - the school was awarded the unesco mozart medal

The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



--- Row 216 | Source: contriever_full_text | Question: Which is a documentary about a satirist, Call Me Lucky or Eclipse of Reason? ---

=== PROMPT START ===
You are a helpful assistant. Follow the user's instructions carefully and answer the question in one or max two sentences. Do not repeat any part of the prompt in your final answer and answer strictly based on provided contexts.

Prompt:
Question:- Which is a documentary about a satirist, Call Me Lucky or Eclipse of Reason?
Contexts:-
[context 1] - in 2007, he directed , an animated feature film of lucky luke.
[context 2] - eclipse of reason is a follow up to nathanson’s first film the silent scream".
[context 3] - his first finished feature-length movie is faq: frequently asked questions, which he released in 2004.
[context 4] - he made his directorial debut with the 2017 film lucky.
[context 5] - he then went on to create the tv pilot lovesick fool which debuted on funnyordie then went on to exhibit at film festivals and is cur

The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.


...


--- Row 1197 | Source: contriever_full_text | Question: What Canadian film producer co-founded CrowdRise? ---

=== PROMPT START ===
You are a helpful assistant. Follow the user's instructions carefully and answer the question in one or max two sentences. Do not repeat any part of the prompt in your final answer and answer strictly based on provided contexts.

Prompt:
Question:- What Canadian film producer co-founded CrowdRise?
Contexts:-
[context 1] - crowdrise is a for profit crowdfunding platform that uses crowdsourcing to raise charitable donations.
[context 2] - crowdrise was founded by edward norton, shauna robertson, and the founders of moosejaw, robert and jeffrey wolfe.
[context 3] - as a co-producer of argo (2012), he received the academy award for best picture in 2013.
[context 4] - co-director tim schwab is an associate professor of film at concordia university.
[context 5] - the film is a feature-length adaptation of his 2012 oscar-winning short film, curfew.

Your task is

The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



--- Row 1198 | Source: contriever_full_text | Question: Are both Vib Gyor and The Futureheads named for albums by The Flaming Lips? ---

=== PROMPT START ===
You are a helpful assistant. Follow the user's instructions carefully and answer the question in one or max two sentences. Do not repeat any part of the prompt in your final answer and answer strictly based on provided contexts.

Prompt:
Question:- Are both Vib Gyor and The Futureheads named for albums by The Flaming Lips?
Contexts:-
[context 1] - vib gyor was a band that was formed in leeds, england.
[context 2] - their name comes from the title of the flaming lips album hit to death in the future head.
[context 3] - they often record lengthy ambient improvisational pieces and release them via imputor?
[context 4] - the futureheads were an english post-punk band from sunderland.
[context 5] - these three songs are still frequently played on hungarian alternative radios.

Your task is to answer the given question by thinking prog

The following generation flags are not valid and may be ignored: ['temperature', 'top_p', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.



--- Row 1199 | Source: contriever_full_text | Question: What film featuring South Korean actress Kim Sung-ryung is a courtroom thriller directed by Sohn Young-sung? ---

=== PROMPT START ===
You are a helpful assistant. Follow the user's instructions carefully and answer the question in one or max two sentences. Do not repeat any part of the prompt in your final answer and answer strictly based on provided contexts.

Prompt:
Question:- What film featuring South Korean actress Kim Sung-ryung is a courtroom thriller directed by Sohn Young-sung?
Contexts:-
[context 1] - the client () is a 2011 south korean courtroom thriller film director by sohn young-sung.
[context 2] - it is a rip-off from the south korean film confession of murder (2012).
[context 3] - kim sung-ryung (born february 8, 1967) is a south korean actress.
[context 4] - his films include south korean hits memories of murder (2003), based on a true-life serial murder case, monster movie the host (2006), and his first englis